In [1]:
import librosa
import numpy as np
import soundfile as sf
import os
from IPython.display import Audio



In [2]:
a=7
a

7

In [3]:
audio1_path = 'BabyElephantWalk60.wav'
audio2_path = 'PinkPanther30.wav'

# Load audio files

audio1, sr1 = librosa.load(audio1_path, sr=None)
audio2, sr2 = librosa.load(audio2_path, sr=None)


In [4]:
if sr1 != sr2:
    raise ValueError("The two audio files must have the same sample rate.")


In [5]:
print("Playing Audio 1:")
Audio(audio1, rate=sr1)


Playing Audio 1:


In [6]:
print("Playing Audio 2:")
Audio(audio2, rate=sr2)

Playing Audio 2:


In [7]:
# Step 3: Extract MFCC features
mfcc1 = librosa.feature.mfcc(y=audio1, sr=sr1, n_mfcc=13)
mfcc2 = librosa.feature.mfcc(y=audio2, sr=sr2, n_mfcc=13)

# Transpose to [frames, coefficients]
mfcc1 = mfcc1.T
mfcc2 = mfcc2.T


In [8]:
os.makedirs('overlapped_audio', exist_ok=True)
os.makedirs('unoverlapped_audio', exist_ok=True)


In [9]:
# Step 4: Define parameters for audio generation
num_files = 1000  # Number of files to generate
min_duration = 2  # Minimum duration in seconds
max_duration = 10 # Maximum duration in seconds


In [10]:

# Step 5: Generate 1000 overlapped and 1000 non-overlapped files
for i in range(num_files):
    # Randomly select duration in seconds between 2 to 10 seconds
    duration = np.random.uniform(min_duration, max_duration)
    num_samples = int(duration * sr1)  # Convert duration to number of samples
    
    # Step 5.1: Non-overlapped audio by merging random segments of audio1 and audio2
    # Select random segments from both audio1 and audio2
    start1 = np.random.randint(0, len(audio1) - num_samples)
    start2 = np.random.randint(0, len(audio2) - num_samples)
    
    segment1 = audio1[start1:start1 + num_samples // 2]  # Take half from audio1
    segment2 = audio2[start2:start2 + num_samples // 2]  # Take half from audio2
    
    # Merge the segments to form a non-overlapped audio file
    non_overlapped_segment = np.concatenate((segment1, segment2))
    
    # Save non-overlapped audio to a file
    non_overlapped_path = f'unoverlapped_audio/audio_unoverlapped_{i+1}.wav'
    sf.write(non_overlapped_path, non_overlapped_segment, sr1)

    # Step 5.2: Overlapped audio generation with the same duration
    start_overlap1 = np.random.randint(0, len(audio1) - num_samples // 2)
    start_overlap2 = np.random.randint(0, len(audio2) - num_samples // 2)
    
    overlapped_segment1 = audio1[start_overlap1:start_overlap1 + num_samples // 2]
    overlapped_segment2 = audio2[start_overlap2:start_overlap2 + num_samples // 2]
    
    overlapped_segment = overlapped_segment1 + overlapped_segment2  # Overlap audio1 and audio2
    
    # Save overlapped audio to a file
    overlapped_path = f'overlapped_audio/audio_overlapped_{i+1}.wav'
    sf.write(overlapped_path, overlapped_segment, sr1)

print("Generated 1000 overlapped and 1000 non-overlapped audio files.")

Generated 1000 overlapped and 1000 non-overlapped audio files.


In [11]:
print("Playing one non-overlapped audio file:")
Audio(filename='unoverlapped_audio/audio_unoverlapped_1.wav', rate=sr1)



Playing one non-overlapped audio file:


In [12]:
print("Playing one overlapped audio file:")
Audio(filename='overlapped_audio/audio_overlapped_1.wav', rate=sr1)

Playing one overlapped audio file:


In [13]:
def extract_mfcc(audio_file, sr=22050, n_mfcc=13):
    # Load the audio file
    y, sr = librosa.load(audio_file, sr=sr)
    # Extract MFCC features
    mfcc = librosa.feature.mfcc(y=y, sr=sr, n_mfcc=n_mfcc)
    # Take the mean across time frames (axis=1)
    mfcc_mean = np.mean(mfcc, axis=1)
    return mfcc_mean


In [14]:
# Path to the folders
overlapped_path = 'overlapped_audio'
non_overlapped_path = 'unoverlapped_audio'

# Lists to store the features and labels
features = []
labels = []

# Extract features from overlapped audio and label them as 1
for file in os.listdir(overlapped_path):
    if file.endswith('.wav'):
        file_path = os.path.join(overlapped_path, file)
        mfcc = extract_mfcc(file_path)
        features.append(mfcc)
        labels.append(1)  # 1 for overlapped

# Extract features from non-overlapped audio and label them as 0
for file in os.listdir(non_overlapped_path):
    if file.endswith('.wav'):
        file_path = os.path.join(non_overlapped_path, file)
        mfcc = extract_mfcc(file_path)
        features.append(mfcc)
        labels.append(0)  # 0 for non-overlapped

# Convert features and labels to numpy arrays
X = np.array(features)
y = np.array(labels)


In [15]:
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import accuracy_score

# Split the data into training and testing sets (80% train, 20% test)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Create a Gaussian Naive Bayes model
nb_model = GaussianNB()

# Train the model
nb_model.fit(X_train, y_train)

# Predict on the test set
y_pred = nb_model.predict(X_test)

# Evaluate the model
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy: {accuracy * 100:.2f}%")


Accuracy: 90.50%


In [16]:
from sklearn.metrics import confusion_matrix, classification_report

# Confusion Matrix
cm = confusion_matrix(y_test, y_pred)
print("Confusion Matrix:")
print(cm)

# Classification Report
print("Classification Report:")
print(classification_report(y_test, y_pred))


Confusion Matrix:
[[173  28]
 [ 10 189]]
Classification Report:
              precision    recall  f1-score   support

           0       0.95      0.86      0.90       201
           1       0.87      0.95      0.91       199

    accuracy                           0.91       400
   macro avg       0.91      0.91      0.90       400
weighted avg       0.91      0.91      0.90       400



In [26]:
# Load the necessary libraries
import librosa
import numpy as np

# Function to extract MFCC features from a new audio file
def extract_mfcc_from_new_audio(audio_file, sr=22050, n_mfcc=13):
    # Load the audio file
    y, sr = librosa.load(audio_file, sr=sr)
    # Extract MFCC features
    mfcc = librosa.feature.mfcc(y=y, sr=sr, n_mfcc=n_mfcc)
    # Take the mean across time frames (axis=1)
    mfcc_mean = np.mean(mfcc, axis=1)
    return mfcc_mean

# Provide the path to your new audio file
new_audio_path = 'preamble.wav'

# Extract MFCC features from the new audio file
new_audio_features = extract_mfcc_from_new_audio(new_audio_path)
Audio(new_audio_path)

In [27]:
# Reshape the features to match the model input (1 sample, n_features)
new_audio_features = new_audio_features.reshape(1, -1)


In [28]:
# Predict the class (0 for non-overlapped, 1 for overlapped) for the new audio file
predicted_label = nb_model.predict(new_audio_features)

# Print the result
if predicted_label[0] == 1:
    print("The audio is overlapped.")
else:
    print("The audio is non-overlapped.")


The audio is non-overlapped.


In [29]:
# Predict the probability of the classes (overlapped or non-overlapped)
predicted_prob = nb_model.predict_proba(new_audio_features)
print(f"Probability of being non-overlapped: {predicted_prob[0][0]:.2f}")
print(f"Probability of being overlapped: {predicted_prob[0][1]:.2f}")


Probability of being non-overlapped: 0.99
Probability of being overlapped: 0.01
